# BM25 algorithm only

In [65]:
import os
import pandas as pd

from tqdm.auto import tqdm
from haystack_integrations.document_stores.elasticsearch import ElasticsearchDocumentStore
from haystack_integrations.components.retrievers.elasticsearch import ElasticsearchBM25Retriever
from haystack import Document
from haystack import Pipeline
from huggingface_hub import hf_hub_download

In [103]:
dataset_path = 'datasets/'
script_variant = 'bm25/'

## Download datasets

In [67]:
passages_allegro_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="allegro-faq", filename="passages.jl", repo_type="dataset")
questions_allegro_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="allegro-faq", filename="questions-test.jl", repo_type="dataset")
passages_legal_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="legal-questions", filename="passages.jl", repo_type="dataset")
questions_legal_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="legal-questions", filename="questions-test.jl", repo_type="dataset")
passages_wiki_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="wiki-trivia", filename="passages.jl", repo_type="dataset")
questions_wiki_source = hf_hub_download(repo_id="piotr-rybak/poleval2022-passage-retrieval-dataset", subfolder="wiki-trivia", filename="questions-test.jl", repo_type="dataset")


## Lauch ElasticSearch in Docker

In terminal when in root directory run:
- docker-compose up

In [94]:
document_store = ElasticsearchDocumentStore(hosts='http://localhost:9200')

def delete_documents(verbose=False):
    document_ids = [document.id for document in document_store.filter_documents(filters={})]
    if verbose:
        print("Deleting document ids: ")
        for document_id in document_ids:
            print(document_id)
    document_store.delete_documents(document_ids=document_ids)
    
delete_documents()

## Index Passages

In [97]:
from haystack.document_stores.types.policy import DuplicatePolicy

passages_allegro = pd.read_json(passages_allegro_source, lines=True, chunksize=int(1e6))
passages_wiki = pd.read_json(passages_wiki_source, lines=True, chunksize=int(1e6))
passages_legal = pd.read_json(passages_legal_source, lines=True, chunksize=int(1e6))

def write_to_document_store(passages):
    for batch in tqdm(passages):
        if 'title' in batch:
            batch['title'] = batch['title'].fillna('')
            batch['text'] = batch.apply(lambda r: r['title'] + ' ' + r['text'], axis=1)
        
        batch = batch.rename(columns={'id': 'passage-id', 'text': 'content'})
        batch_as_dicts = batch.to_dict(orient='records')
        documents_list = [Document(content=str(passageDict['content']), id=str(passageDict['passage-id'])) for passageDict in batch_as_dicts]
        document_store.write_documents(documents_list, policy=DuplicatePolicy.SKIP)

write_to_document_store(passages_allegro)

0it [00:00, ?it/s]

In [98]:
document_store.count_documents()

921

## Retrieve Similar Passages

In [99]:
# Use a retriever that utilizes BM25 algorithm (bag-of-words based)
retriever = ElasticsearchBM25Retriever(document_store=document_store)

pipe = Pipeline()
pipe.add_component("retriever", retriever)

In [100]:
questions_allegro = pd.read_json(questions_allegro_source, lines=True)
print(questions_allegro.shape)
questions_wiki = pd.read_json(questions_wiki_source, lines=True)
print(questions_wiki.shape)
questions_legal = pd.read_json(questions_legal_source, lines=True)
print(questions_legal.shape)

(900, 2)
(1291, 2)
(718, 2)


In [101]:
def run_pipe(questions):
    preds = []
    
    for _, row in tqdm(questions.iterrows()):
        top_passages = pipe.run({"retriever": {"query": row['text']}})
        
        for passage in top_passages['retriever']['documents']:
            passage = passage.to_dict()
            preds.append({
                'question-id': row['id'],
                'passage-id': passage['id'],
                'score': passage['score'],
            })
    
    return pd.DataFrame(preds)

preds_allegro = run_pipe(questions_allegro)

delete_documents()
write_to_document_store(passages_legal)

preds_legal = run_pipe(questions_legal)

delete_documents()
write_to_document_store(passages_wiki)

preds_wiki = run_pipe(questions_wiki)


0it [00:00, ?it/s]

{'retriever': {'documents': [Document(id=821, content: 'Dodatkowa prowizja od sprzedaży w wyróżnionych ofertach obowiązuje w kategoriach objętych standardow...', score: 58.431038), Document(id=685, content: 'Naliczamy każdorazowo w chwili sprzedaży, podobnie jak w przypadku standardowej prowizji od sprzedaż...', score: 44.65083), Document(id=6, content: 'Dodatkową prowizję od sprzedaży w wyróżnionych ofertach naliczamy we wszystkich ofertach z aktywną o...', score: 34.49206), Document(id=509, content: 'Wysokość prowizji od sprzedaży nie jest jednakowa dla wszystkich ofert. Zależy od
* ceny końcowej, z...', score: 26.200457), Document(id=218, content: 'Dodatkową prowizję zwrócimy Ci na takich samych zasadach, jak standardową prowizję od sprzedaży.', score: 25.066103), Document(id=379, content: 'Tak, dodatkowa prowizja obowiązuje konta zwykłe oraz konta Firma.', score: 22.03932), Document(id=869, content: 'Z każdą pozytywną weryfikacją lub przedłużeniem statusu Super Sprzedawcy o kolejne

0it [00:00, ?it/s]

0it [00:00, ?it/s]

{'retriever': {'documents': [Document(id=1997_553_345, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 69.3492), Document(id=1997_553_136, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 51.298702), Document(id=1997_553_135, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 49.62758), Document(id=1997_553_346, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 44.708622), Document(id=1997_553_339, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 43.517002), Document(id=1997_553_223, content: 'Ustawa z dnia 6 czerwca 1997 r. Kodeks karny CZĘŚĆ OGÓLNA Rozdział I Zasady odpowiedzialności karnej...', score: 43.289467), Document

0it [00:00, ?it/s]

0it [00:00, ?it/s]

{'retriever': {'documents': [Document(id=975180-0, content: 'Zawiadomienie o niepopełnionym przestępstwie Zawiadomienie o niepopełnionym przestępstwie – przestęp...', score: 52.93671), Document(id=565763-0, content: 'Alibi Alibi (łac. "gdzie indziej") – dowód w postępowaniu karnym na okoliczność, że podejrzany albo ...', score: 45.95068), Document(id=61574-9, content: 'Przestępstwo Kara stanowi odpłatę za popełnione przestępstwo, a jej miarą jest ciężar przestępstwa i...', score: 45.913647), Document(id=1994959-40, content: 'Crimen sollicitationis Gdy molestowana podczas spowiedzi osoba jest dzieckiem czy osobą nieletnią, m...', score: 45.05569), Document(id=176418-9, content: 'Recydywa Ważne jest tylko to, by sprawca odbył karę za poprzednie przestępstwo w wymiarze co najmnie...', score: 44.123528), Document(id=1121-3, content: 'Dowód (matematyka) Dowód nie wprost (dowód apagogiczny) polegający na przyjęciu, że twierdzenie jest...', score: 39.870255), Document(id=433856-0, content: 'P

In [104]:
preds_allegro.to_csv(os.path.join(dataset_path + 'allegro/', script_variant + 'submission.tsv'), sep='\t', index=False)
preds_wiki.to_csv(os.path.join(dataset_path + 'wiki/', script_variant + 'submission.tsv'), sep='\t', index=False)
preds_legal.to_csv(os.path.join(dataset_path + 'legal/', script_variant + 'submission.tsv'), sep='\t', index=False)


## Evaluate

`o evaluate the results, run these in terminal:`

### allegro:
`python ./eval.py --true datasets/allegro/pairs-test.tsv --pred datasets/allegro/bm25/submission.tsv`

Result: 
NDCG@10: 0.493

### wiki
`python ./eval.py --true datasets/wiki/pairs-test.tsv --pred datasets/wiki/bm25/submission.tsv`

Result: 
NDCG@10: 0.185

### legal
`python ./eval.py --true datasets/legal/pairs-test.tsv --pred datasets/legal/bm25/submission.tsv`

Result: 
NDCG@10: 0.696